# QURI Chemistry: QunaSys による Qiskit Function 

{/* cspell:ignore QSCI, CCSD, UCCSD, imags, CCGSD, CISD */}

<Admonition type="note">
  Qiskit Functions は、IBM Quantum™ Premium Plan ユーザーのみが利用できる実験的な機能です。プレビュー リリースの状態であり、変更される可能性があります。
</Admonition>

## 概要

このfunctionは、[量子選択構成相互作用 (Quantum Selected Configuration Interaction, QSCI) アルゴリズム](https://arxiv.org/pdf/2302.11320)に基づく 2 つのアルゴリズムのいずれかを使用して、量子化学の基底状態推定問題を解決するのに役立ちます：

*   QSCI
*   最適化ベースの QSCI

このfunctionsを使用するための全体的な手順は、以下のフローチャートにまとめられています：

![Workflow](./images/guides/qunasys-qsci/workflow.svg)



## 機能説明

QSCIアルゴリズムは、量子コンピューター上の特定のansatzからサンプリングします。サンプリングされた各ビット列は電子配置に対応し、ビット列がサンプリングされた回数はその電子配置の重要度を表します。$R$ という数を選ぶと、サンプルの中から $R$ 個の最も重要な電子配置を選ぶことができます。この function は $R$ の選択に応じて部分空間ハミルトニアンを構成し対角化します。最小の固有値は 「QSCIエネルギー」と呼ばれ、QSCIアルゴリズムの真の基底状態エネルギーの推定値となります。

QSCIの重要な要素の一つは初期状態の準備です。この function では、いくつかの可能な初期状態準備が提供されています。これらには、[hardware efficient](https://www.nature.com/articles/nature23879), [UCCSD](https://www.nature.com/articles/srep03589), [kUpCCGSD](https://arxiv.org/abs/1810.02327), [kuCJ](https://arxiv.org/abs/1909.12410)が含まれます。CCSD振幅ベースの二重励起 ansatz は、特に近い将来のデバイスで実行するために提供されています。Ansatz 固有の設定も提供されており、必要に応じてカスタマイズすることができます。

QSCIエネルギーを返すだけでなく、この function は推定基底状態波動関数を計算し、重要な電子配置を特定するのに役立ちます。



## 始めてみましょう

まず、 [IBM Quantum API token](http://quantum.ibm.com/) を使用して認証し、次のように Qiskit Function を選択します。

In [1]:
from qiskit_ibm_runtime import QiskitRuntimeService
from qiskit_ibm_catalog import QiskitFunctionsCatalog

token = QiskitRuntimeService.saved_accounts()["default-ibm-quantum"]["token"]
catalog = QiskitFunctionsCatalog(token=token)

function = catalog.load("qunasys/quri-chemistry")

次の引数を使用して function を呼び出します：

```python
function.run(
    method = ...,       # Allow only "QSCI" or "OPT_QSCI"
    parameters = {...}, # A JSON dictionary representing all the algorithm setting
    instance = ...,     # Your instance string.
    backend = ...       # The backend name you want to use.
)
```



各引数の詳細な説明を次の表にまとめます。

|名前	|タイプ	|説明	|必須	|デフォルト	|例|
| :--------- | :--- | :-------------------------------- | :------- | :---------------------------------- | :---------------- |
| method     | str  | アルゴリズム名                | Yes      | -                                   | “QSCI”            |
| parameters | json | アルゴリズムの詳細設定 | Yes      | -                                   |                   |
| instance   | str  | インスタンス名                | No       | Your default instance saved on disk | “ibm-q/open/main” |
| backend    | str  | 使用したいBackend名  | No       | The least busy one available        | “ibm\_torino”     |



## 分子を設定する

ここでは分子の作り方を学びます。入力は `pyscf.gto.M` と全く同じですが、`active_space` オプションが追加されています。以下は分子を構成するための詳細な設定をまとめたものです。

|名前	|タイプ	|説明	|必須	|デフォルト	|例|
| :------------ | :---- | :--------------------------------------------------------------------------------------------------------------------------------------------------------------- | :------- | :------- | :------------------------------------------------------------- |
| atom          | str   | 原子座標のリスト                                                                                                                                     | Yes      | -        | “H 0 0 0; H 0 0 1”                                             |
| basis         | str   | 電子波動関数を表す基底関数。許容される値は[PySCF](https://pyscf.org/_modules/pyscf/gto/basis.html) でサポートされている値と同じ。| No       | “sto-3g” | “sto-3g”                                                       |
| spin          | float |  分子の $s_z$ 量子数。 spin=0.0 のみサポート。                                                                                           | No       | 0.0      | 0.0                                                            |
| charge        | int   | 分子の総電荷                                                                                                                               | No       | 0        | 0                                                              |
| active\_space | json  | 選択するアクティブスペース。詳細は、次の「アクティブスペース」表を参照。                                                            | No       | None     | 詳細は、次の「アクティブスペース」表を参照。                                                |


アクティブスペースの設定を以下にまとめます。


|名前	|タイプ	|説明	|必須	|デフォルト	|例|
| :-------------------- | :--------- | :----------------------------------------- | :------- | :------ | :--------- |
| n\_active\_ele        | int        | 活性電子の数             | Yes      | -       | 4          |
| n\_active\_orb        | int        | 活性空間軌道の数      | Yes      | -       | 3          |
| active\_orbs\_indices | list\[int] | 活性空間軌道インデックスのリスト | No       | None    | \[0, 1, 2] |

例として、$H_2O$ 分子の設定をJSON形式で行うことができます：


In [3]:
mole = {
    "atom": "O 0 0 0; H 0.2774 0.8929 0.2544; H 0.6068 -0.2383 -0.7169",
    "basis": "6-31g",   # default to "sto-3g"
    "spin": 0.0,        # default to 0.0. Current code forces spin = 0.0
    "charge": 0,        # default to 0
    "active_space": {   # default to None. Equivalent to no active space chosen.
        "n_active_ele": 10,
        "n_active_orb": 10,
        "active_orbs_indices": [i for i in range(10)]
    }
}

## アルゴリズムを実行する

すべての関数入力は JSON 形式です。アルゴリズムを実行するためのオプションを指定する JSON 文字列を設定します。前述のように、提供されるアルゴリズムには "QSCI" と "OPT\_QSCI" の 2 種類があります。




### QURI Chemistry

QURI Chemistry では、ansatz、その設定、状態準備手法、および QSCI 設定を指定する必要があります。一般的な QSCI 入力例:

```
algo_input = {
    "mole": mole,
    "ansatz": ...,
    "state_prep_method": ...,
    "ansatz_setting": ...,
    "qsci_setting": {"n_shots": ..., "number_of_states_pick_out": ...},
    "mitigation_setting": {}
},

```

|名前	|タイプ	|説明	|必須	|デフォルト	|例|
| :------------------ | :-------------- | :------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------- | :------- | :------ | :-------------------------------------------------------------- |
| mole                | json            | The molecule setting. See the table for setting molecules above                                                                                                                                                | Yes      |         | The molecule setting. See the table for setting molecules above |
| ansatz              | str             | The name of the ansatz you want to use. Only “DoubleExcitation” and “UCCSD” are supported. `DoubleExcitation` is highly recommended to obtain a stable result, especially for systems larger than eight qubits | Yes      |         | “DoubleExcitation”                                              |
| state\_prep\_method | str             | The way you want to prepare the circuit parameter of your ansatz. Only CCSD is allowed                                                                                                                         | No       | “CCSD"  | “CCSD”                                                          |
| ansatz\_setting     | str             | Specific setting you want to configure your ansatz with                                                                                                                                                        | No       | None    | See the following examples                                      |
| qsci\_setting       | dict\[str, int] | Specify the number of shots and the size of the subspace. See the following section for details                                                                                                                | Yes      |         | See the QSCI setting table                                      |
| mitigation\_setting | json            | Settings for configuring error mitigation                                                                                                                                                                      | No       | None    | See the mitigation section below                                |



#### QSCIアルゴリズムパラメータ
QSCI アルゴリズムを設定するためのパラメータがこの表にまとめられています。

|名前	|タイプ	|説明	|必須	|例|
| :---------------------------- | :--- | :-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------- | :------- | :------ |
| n\_shots                      | int  | ansatz からサンプリングするショットの総数                                                                                                                                                                                                                                                                     | Yes      | 100000  |
| number\_of\_states\_pick\_out | int  | 部分空間ハミルトニアン$R$のサイズを表します。これは*古典的*リソースに影響し、ansatzからサンプリングされたビット文字列の数($n$)が$R$より大きい場合、$R \times R$部分空間ハミルトニアンの*古典的*対角化が実行されます。それ以外の場合は、$n \times n$部分空間行列が対角化されます。| Yes      | 10000   |


この例では、次の設定を示します：


In [4]:
qsci_setting = {"n_shots": 1e5, "number_of_states_pick_out": 1e4}

#### UCCSD を使った QURI Chemistry 

UCCSD は、化学にヒントを得た一般的な仮説です。QURI Chemistry function では、 `ansatz_setting` キーを使用してカスタマイズできます。UCCSD をカスタマイズするためのオプションは、下の表にまとめられています。

|名前	|タイプ	|説明	|必須	|デフォルト |例|
| :---------------- | :--- | :------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------- | :------- | :------ | :------ |
| use\_singles      | bool | Trueの場合、すべての単一励起モードが含まれる。それ以外の場合は、すべてオフ。                                                                                                                                                   | No       | True    | True    |
| n\_trotter        | int  | 指数励起演算子のトロッターステップ数                                                                                                                                                             | No       | 1       | 1       |
| reduce\_parameter | bool | QSCIではTrueのみが許可される。[QURI Parts documentation](https://quri-parts.qunasys.com/api/quri_parts/openfermion/quri_parts.openfermion.ansatz#quri_parts.openfermion.ansatz.TrotterUCCSD) `singlet_excitation`のフィールドを参照してください。| No       | True    | True    |

UCCSD で QURI Chemistry を実行するための辞書:


In [ ]:
qsci_uccsd_json = {
    "mole": mole,
    "ansatz": "UCCSD",
    "state_prep_method": "CCSD",    # this is optional and defaulted to "CCSD".
    "ansatz_setting": {"use_singles": False},   # this is optional and defaulted to the list above.
    "qsci_setting": {"n_shots": 1e5, "number_of_states_pick_out": 1e4},
}

#### 二重励起 ansatz を用いた QURI Chemistry 

`DoubleExcitation` を ansatz として選択した場合、`ansatz_setting` フィールドの `n_amplitudes` キーを使用して、含める励起振幅の数を指定できます。デフォルト値は 10 です。この function は、CCSD 振幅を大きさに応じて並べ替え、最大の `n_amplitudes` を選択して ansatz を構築します。この ansatz を使用した JSON 辞書の例を次に示します。

In [5]:
qsci_double_exc_json = {
    "mole": mole,
    "ansatz": "DoubleExcitation",
    "state_prep_method": "CCSD",    # this is optional and defaulted to "CCSD".
    "ansatz_setting": {"n_amplitudes": 20}, # this is optional and defaulted to {"n_amplitudes": 10}.
    "qsci_setting": {"n_shots": 1e5, "number_of_states_pick_out": 5e4},
    "mitigation_setting": {     # please refer to the "error mitigation" section of this tutorial.
        "configuration_recovery": {
            "number_of_states_pick_out": 10000
        }
    }
}

#### QSCIを実行する
 `QSCI` アルゴリズムの実行例:


In [30]:
import datetime
import time
job = function.run(
    method="QSCI",
    parameters=qsci_double_exc_json,
    instance="INSTANCE",
    backend="ibm_strasbourg",
)

while True:
    try:
        print(datetime.datetime.now(), job.status())
        time.sleep(10)
        if job.status() in ["ERROR", "DONE"]:
            break
    except:
        print("Retrieve job status failed.")
        pass

result = job.result()

2024-08-27 23:01:36.090958 QUEUED
2024-08-27 23:01:49.358961 QUEUED
2024-08-27 23:02:02.713788 QUEUED
2024-08-27 23:02:15.481531 RUNNING
2024-08-27 23:02:28.200317 RUNNING
2024-08-27 23:02:41.446378 RUNNING
2024-08-27 23:02:54.563686 RUNNING
2024-08-27 23:03:07.706745 RUNNING
2024-08-27 23:03:20.400988 RUNNING
2024-08-27 23:03:33.708046 RUNNING
2024-08-27 23:03:46.656525 RUNNING
2024-08-27 23:03:59.385160 RUNNING
2024-08-27 23:04:12.528769 RUNNING
2024-08-27 23:04:25.625868 RUNNING
2024-08-27 23:04:38.718299 RUNNING
2024-08-27 23:04:51.828514 RUNNING
2024-08-27 23:05:04.745142 RUNNING
2024-08-27 23:05:17.727985 RUNNING
2024-08-27 23:05:31.061746 RUNNING
2024-08-27 23:05:43.821970 RUNNING
2024-08-27 23:05:56.897187 RUNNING
2024-08-27 23:06:10.088404 RUNNING
2024-08-27 23:06:22.959995 RUNNING
2024-08-27 23:06:35.873720 RUNNING
2024-08-27 23:06:48.798231 RUNNING
2024-08-27 23:07:02.731781 RUNNING
2024-08-27 23:07:15.819290 RUNNING
2024-08-27 23:07:29.360154 RUNNING
2024-08-27 23:07:42.341

実行結果をプリントすることができます:



In [41]:
print(result)

{'qsci_energy': -76.05077853515165, 'state_vector': {'bits': [1023, 131583, 3039, 3063, 2943, 33663, 263163, 9087, 2043, 33759, 66303, 525183, 263151, 17403, 2031, 525303, 263103, 9207, 1983, 5115, 33783, 9183, 5055, 5103, 17343, 17391, 525279, 139647, 70383, 18411, 67311, 164319, 139767, 655839, 164343, 655743, 267243, 527319, 6123, 533367, 133623, 11127, 41847, 279531, 82683, 67263, 533343, 82671, 133503, 264171, 11103, 35703, 41823, 67323, 527199, 164223, 133599, 35679, 393855, 328383, 533463, 264111, 328431, 279483, 267183, 132735, 21483, 139743, 557919, 328443, 265083, 18351, 41943, 35799, 132591, 557943, 141687, 11223, 197595, 21423, 50043, 527223, 655863, 21435, 279471, 558039, 82623, 6075, 6063, 98943, 70335, 70395, 141663, 25455, 265179, 10107, 6399, 267195, 393723, 148191, 197583, 197439, 7131, 18363, 295923, 3963, 535383, 265203, 25407, 526239, 329403, 264447, 590331, 196863, 270591, 688503, 526287, 344763, 25467, 19359, 787323, 148095, 132855, 43863, 34047, 393951, 265071, 

QSCI エネルギーを確認するには、"qsci\_energy" キーを使用します：


In [48]:
CASCI_ENERGY = -76.0508056368444    # Exact result
qsci_energy = result["qsci_energy"]
print(f"CASCI energy: {CASCI_ENERGY} Ha")
print(f"QSCI energy: {qsci_energy} Ha")
print(f"Energy error: {(qsci_energy - CASCI_ENERGY) * 1000: .2e} mHa")

CASCI energy: -76.0508056368444 Ha
QSCI energy: -76.05077853515165 Ha
Energy error:  2.71e-02 mHa


返された $\text{H}_2 \text{O}$ 分子の基底状態エネルギー推定値は、正確な結果に非常に近いです!

`state_vector` フィールドには、`bits`、`reals`、および `imags` の 3 つの値が含まれます。`bits` 値は、電子配置を表す整数のリストです。`reals` (`imags`) フィールドの $i$ 番目の位置は、位置 $i$ の電子配置の振幅の実数 (虚数) 部分を表します。これを大きさでソートし、最も重要な上位 10 個の電子配置をプリントできます。



In [66]:
import numpy as np

amps = np.array(result["state_vector"]["reals"]) + 1j * np.array(result["state_vector"]["imags"])
sort_idx = np.argsort(np.abs(amps))

for i, (bit, real, imag) in enumerate(zip(
    np.array(result["state_vector"]["bits"])[sort_idx][::-1],
    np.array(result["state_vector"]["reals"])[sort_idx][::-1],
    np.array(result["state_vector"]["imags"])[sort_idx][::-1],
)):
    if i > 20:
        break
    print(
        f"Electron configuration: {bin(bit)[2:].zfill(20)}, "
        f"amplitude: {real + 1j * imag: .3e}, "
        f"magnitude: {real**2 + imag**2: .3e}"
    )

Electron configuration: 00000000001111111111, amplitude: -7.671e-01+6.185e-01j, magnitude:  9.710e-01
Electron configuration: 00110000000011111111, amplitude:  4.492e-02-3.622e-02j, magnitude:  3.330e-03
Electron configuration: 00000011001111001111, amplitude:  3.379e-02-2.724e-02j, magnitude:  1.884e-03
Electron configuration: 00001100001111001111, amplitude:  2.247e-02-1.812e-02j, magnitude:  8.333e-04
Electron configuration: 00100001000111101111, amplitude: -2.172e-02+1.751e-02j, magnitude:  7.780e-04
Electron configuration: 00010010001011011111, amplitude: -2.171e-02+1.750e-02j, magnitude:  7.775e-04
Electron configuration: 00000001101101101111, amplitude: -2.006e-02+1.617e-02j, magnitude:  6.637e-04
Electron configuration: 00000010011110011111, amplitude: -2.005e-02+1.617e-02j, magnitude:  6.636e-04
Electron configuration: 00000000111100111111, amplitude:  1.980e-02-1.596e-02j, magnitude:  6.467e-04
Electron configuration: 11000000001111001111, amplitude:  1.950e-02-1.572e-02j, ma

### 最適化ベースのQSCI

CCSD を状態準備方法として使用したくない、または CCSD 初期状態からさらに最適化したい場合は、最適化ベースの QSCI を使用できます。このアルゴリズムを使用すると、ランダムな初期パラメータを持つ、より化学にヒントを得た ansatz にアクセスできます。以下は、ansatz とそれに対応するサポートされている状態準備手法の表です：

| Ansatz             | 準備手法     | Ansatz 設定のデフォルト                                    | 注記                                               |
| ------------------ | ---------------------- | ----------------------------------------------------------- | ----------------------------------------------------- |
| 二重励起  | CCSD                   | `{n_amplitudes: 10}`                                        | 最後の例の結果から最適化させる |
| UCCSD              | CCSD (default), Random | `{use_singles: True, n_trotter: 1, reduce_parameter: True}` |  8量子ビット以上のシステムには推奨しない |
| KuCJ               | Random                 | `{k: 1}`                                                    | 16量子ビットまでのシステムに推奨                |
| KUpCCGSD           | Random                 | `{k: 1, n_trotter: 1, reduce_parameter: False} `            |                                                       |
| Hardware Efficient | Random                 | `{n_layers: depend on qubit size}        `                  |                                                       |

準備手法と ansatz 設定を指定しない場合は、デフォルト値が使用されます。このアルゴリズムでは、QSCI エネルギーが COBYLA オプティマイザーのコスト関数として使用されます。各反復で、回路パラメーターが更新され、QSCI エネルギーが新しい回路パラメーターセットを含む回路で評価されます。

このアルゴリズムを実行するために使用される JSON 辞書は、QSCI のものと似ています。リソース使用量を制限するための追加フィールド "max\_iter" が 1 つ含まれています。デフォルトは 2000 回の反復です。

以下は、1-uCJ ansatz を使用してこのアルゴリズムを実行した例です：

In [86]:
opt_qsci_1ucj_json = {
    "mole": mole,
    "ansatz": "KuCJ",
    "state_prep_method": "RANDOM",  # this is optional and defaulted to "RANDOM" for "KuCJ".
    "ansatz_setting": {"k": 1},     # this is optional and defaulted to the table above.
    "qsci_setting": {
        "n_shots": 1e5, "number_of_states_pick_out": 5e4
    },
    "max_iter": 5,                  # Default to 2000. Choose 5 iteration for demonstration.
    "mitigation_setting": {         # Refer to the "error mitigation" section.
        "configuration_recovery": {
            "number_of_states_pick_out": 10000
        }
    }
}

In [ ]:
import time
opt_job = function.run(
    method="OPT_QSCI",
    parameters="opt_qsci_1ucj_json",
    instance="ibm_strasbourg",
)
start = time.time()

while True:
    try:
        print(datetime.datetime.now(), opt_job.status())
        time.sleep(10)
        if opt_job.status() in ["ERROR", "DONE"]:
            break
    except:
        print("Retrieve job status failed.")
        pass

opt_result = opt_job.result()

結果をプリントすることができます。





In [80]:
print(opt_result)

{'qsci_energy': -76.05051672600099, 'state_vector': {'bits': [1023, 1983, 2943, 33783, 3039, 263151, 33663, 2031, 5103, 9087, 525183, 33759, 2043, 17343, 9207, 9213, 525279, 17406, 131583, 5115, 525303, 263163, 525309, 17391, 9183, 3063, 263103, 66303, 3069, 2046, 17403, 263166, 5118, 33789, 5055, 67323, 133503, 70335, 264123, 655863, 67263, 279471, 139743, 6138, 67311, 655743, 133599, 139647, 11127, 164223, 267195, 527223, 18411, 18426, 533343, 558039, 82671, 21486, 264111, 267183, 11223, 328443, 328446, 70383, 328431, 35799, 533373, 6063, 527199, 11103, 6126, 21483, 533469, 18363, 279534, 67326, 41847, 533463, 279486, 655839, 533367, 133629, 70398, 11229, 21498, 558045, 11133, 82683, 21423, 41823, 139767, 527319, 35679, 557919, 264126, 164343, 10095, 35703, 267243, 655869, 267198, 21435, 328383, 279531, 527325, 271356, 6075, 18366, 83631, 164349, 264171, 557943, 271311, 83691, 139773, 527229, 6078, 133623, 13215, 82686, 6123, 68319, 41949, 279546, 35805, 21438, 18414, 270591, 279483,

返される結果には、QSCI の例と同じフィールドが含まれます。

In [91]:
CASCI_ENERGY = -76.0508056368444    # Exact result
opt_qsci_energy = opt_result["qsci_energy"]
print(f"CASCI energy: {CASCI_ENERGY} Ha")
print(f"QSCI energy: {opt_qsci_energy} Ha")
print(f"Energy error: {(opt_qsci_energy - CASCI_ENERGY) * 1000: .2e} mHa")
print()
print("Top 20 important configurations:")
amps = np.array(opt_result["state_vector"]["reals"]) + 1j * np.array(opt_result["state_vector"]["imags"])
sort_idx = np.argsort(np.abs(amps))

for i, (bit, real, imag) in enumerate(zip(
    np.array(opt_result["state_vector"]["bits"])[sort_idx][::-1],
    np.array(opt_result["state_vector"]["reals"])[sort_idx][::-1],
    np.array(opt_result["state_vector"]["imags"])[sort_idx][::-1],
)):
    if i > 20:
        break
    print(
        f"Electron configuration: {bin(bit)[2:].zfill(20)}, "
        f"amplitude: {real + 1j * imag: .3e}, "
        f"magnitude: {real**2 + imag**2: .3e}"
    )

CASCI energy: -76.0508056368444 Ha
QSCI energy: -76.05051672600099 Ha
Energy error:  2.89e-01 mHa

Top 20 important configurations:
Electron configuration: 00000000001111111111, amplitude: -1.934e-01-9.664e-01j, magnitude:  9.713e-01
Electron configuration: 00110000000011111111, amplitude:  1.127e-02+5.629e-02j, magnitude:  3.295e-03
Electron configuration: 00000011001111001111, amplitude:  8.434e-03+4.214e-02j, magnitude:  1.847e-03
Electron configuration: 00001100001111001111, amplitude:  5.640e-03+2.818e-02j, magnitude:  8.258e-04
Electron configuration: 00010010001011011111, amplitude: -5.445e-03-2.721e-02j, magnitude:  7.698e-04
Electron configuration: 00100001000111101111, amplitude: -5.418e-03-2.707e-02j, magnitude:  7.622e-04
Electron configuration: 00000010011110011111, amplitude: -5.053e-03-2.524e-02j, magnitude:  6.628e-04
Electron configuration: 00000001101101101111, amplitude: -5.023e-03-2.510e-02j, magnitude:  6.551e-04
Electron configuration: 00000000111100111111, amplit

## エラー緩和

通常、手元の問題は、特に粒子数とスピンの保存など、ある程度の対称性を尊重する必要があります。対称性を復元するには、対称事後選択または[構成回復](https://arxiv.org/pdf/2405.05068v1)エラー緩和を使用します。どちらのアルゴリズムでも、 "mitigation\_setting" フィールドを使用してどちらかを選択できます。対称事後選択がデフォルト値です。

事後選択では、誤った状態を完全に削除し、サブスペース ハミルトニアンを構築するための基底状態のみを残します。これにより、通常は古典的なリソースが節約されますが、多くの状態が失われる可能性があります。構成回復では、誤った基底状態の個々のビットを、ある確率分布に関して反転しようとします。構成回復を使用すると、より大きなサブスペース ハミルトニアンを構築するために基底状態の数が増えますが、より多くの古典的なリソースが使用されます。

|名前	|タイプ	|説明	|必須	|デフォルト|
| :------------------------- | :---------------------------- | :--------------------------------------------------------------------------------------------------------------------------------------- | :------- | :------ |
| particle\_number\_symmetry | bool                          | Trueの場合、粒子数保存を尊重しないビット文字列をサンプリング結果から削除する。| No       | TRUE    |
| spin\_symmetry             | bool                          | Trueの場合、サンプリング結果から$s_z$保存を無視するビット列を削除する。                                                | No       | TRUE    |
| configuration\_recovery    | Union\[bool, dict\[str, int]] | False以外の値に設定されている場合、構成回復を有効にする。dict[str, int]入力については、構成回復セクションを参照してください。 | No       | FALSE   |



### 選択後の対称性

以下のキーは、対称性ポスト選択を制御します: `particle_number_symmetry` と `spin_symmetry`。`particle_number_symmetry` を True に設定すると、総電子数を保存する状態が選択されます。`spin_symmetry` を True に設定すると、$s_z$ 量子数を保存する状態が選択されます。現在、$s_z = 0$ のみがサポートされています。デフォルトは次のとおりです:


In [ ]:
mitigation_setting = {
    "particle_number_symmetry": True,
    "spin_symmetry": True,
}

<Admonition type="note">粒子対称性が False の場合、スピン対称性を True に設定することはできません。
 </Admonition>



### 構成の回復
対称性事後選択の代わりに、構成回復を選択することもできます。構成回復の最も一般的なセットは、以下の表にまとめられています。

| 名前	| タイプ	| 説明	| 必須	| デフォルト| 
| :---------------------------- | :---------- | :------------------------------------------------------------------------------------------------------------------ | :------- | :------ |
| n\_recover\_iteration         | int         | 回復の繰り返し回数                                                                                   | No       | 5       |
| n\_batch                      | int         | 反復ごとに生成されるバッチの数                                                                      | No       | 1       |
| number\_of\_states\_pick\_out | int or None | 回復プロセスにおけるQSCIベクトルの次元。Noneの場合は、QSCIに使用される値と同じに設定される。 | No       | None    |
| recovery\_r\_multiple         | int         | number\_of\_states\_pick\_out の乗数。これは生のサンプルから選択された状態の数です。| No       | 10      |


構成の回復を有効にするには、エラー緩和フィールドで `configuration_recovery = True` を指定するか、上記のいずれかのフィールドをカスタマイズします。例:


In [ ]:
# Use default configuration recovery setting
default_mitigation_setting = {
    "mitigation_setting": {
        "configuration_recovery": True
    }
}

# Customized configuration recovery setting
customized_mitigation_setting = {
    "mitigation_setting": {
        "configuration_recovery": {
            "n_recover_iteration": 20,
            "n_batch": 10,
            "number_of_states_pick_out": 5000
        }
    }
}

<Admonition type="note"> `configuration_recovery` がオンになっている場合、他の緩和方法を有効にすることはできません。 </Admonition>



## パフォーマンス

### $\text{N}_2$ 解離曲線

パフォーマンスのベンチマークとして、20 量子ビットの $\text{N}_2$ 解離曲線をデモンストレーションとして提供します。

![N2\_dissociation](./images/guides/qunasys-qsci/N2_dissociation.svg)

プロット内の赤い曲線は、選択された ansatz `DoubleExcitation`を使用した QSCI 法によって生成されます。窒素原子間の距離 `d` を異なる値に選択して次のコードで再現できます。


In [ ]:
d = 1.0
n2_dissociation_qsci = {
    "mole": {"atom": f"N 0 0 0; N 0 0 {d}",},
    "ansatz": "DoubleExcitation",
    "state_prep_method": "CCSD",
    "qsci_setting": {
        "n_shots": 100000, "number_of_states_pick_out": 50000
    },
    "mitigation_setting": {
        "configuration_recovery": True
    },
}
job = function.run(
    method="QSCI",
    parameters=n2_dissociation_qsci,
    backend="ibm_strasbourg"
)

各ポイントでは通常、QPU の使用に約 1 分かかることに注意してください。古典的な側面では、$R$ は 50000 に選択されていますが、必ずしも $50000 \times 50000$ 行列の対角化が行われることを意味するわけではありません。この場合、構成回復後のサンプル数は約 5000 ～ 7000 で、これによりサブスペース ハミルトニアンの次元が設定されます。したがって、古典的な対角化コストは、一般的な完全構成相互作用 (full configuration interaction, FCI) 計算のコストよりもはるかに小さくなります。

この結果の重要なポイントは、適切な構成回復を備えた QSCI が、すべての `d` の選択で、Hartree-Fock (HF)、CCSD、CISD などのスケーラブルな古典的な方法よりも優れていることです。これは、FCI エネルギーが利用できなくなるスケールでは、QSCI がすべての距離で基底状態エネルギーを推定する信頼性の高い方法として機能することを意味します。例えば、6-31g基底を使用すると、QURI Chemistryによって生成された36量子ビット$\text{N}_2$解離曲線は次のように表されます。

![N2\_dissociation](./images/guides/qunasys-qsci/36_qubit_N2_dissociation.svg)

ここで、FCI 曲線は一般的なラップトップ (M2 Pro チップ、16G RAM) では利用できません。ただし、QSCI は、`ibm_strasbourg` 量子コンピューターとともに、同じマシン上で従来の方法と比較して定性的に正しい解離曲線を生成できます。


### アゾベンゼン

アゾベンゼンには、トランスアゾベンゼンとシスアゾベンゼンという 2 つの異性体があります。2 つの異性体の基底状態間のエネルギー差は、アゾベンゼンの光異性化において重要な役割を果たします。例として、最大 28 量子ビットの異なるアクティブ空間設定で、QSCI と FCI 間の基底状態エネルギー差をベンチマークします。構成回復により、QURI Chemistry は、わずか $10^5$ ショット、30 ～ 40 秒の QPU 使用、およびポイントあたり 10 分未満の従来の後処理時間で、5 mHa 未満のエラーを生成します。


![Azobenzene](./images/guides/qunasys-qsci/azobenzene.svg)



## サポート
20 量子ビットを超える分子については、 [sales@qunasys.com](mailto:sales@qunasys.com) までお問い合わせください。




## 次のステップ

  *   [QunaSys QURI Chemistryへのアクセスをリクエストする](https://quantum.ibm.com/functions?id=42f5a0ea-2c74-4681-a973-3ef97de97ee4)
  *   [QunaSys QURI Chemistry を使用した強結合システムの解離曲線を計算する](https://learning.quantum.ibm.com/tutorial/compute-dissociation-curves-for-strong-coupling-systems-with-quna-sys-qsci) チュートリアルに挑戦してみましょう。


